In [1]:
import pandas as pd
from pyecharts.charts import Line, Bar, Map, Timeline
from pyecharts import options as opts

from pyecharts.globals import CurrentConfig, NotebookType
CurrentConfig.NOTEBOOK_TYPE = NotebookType.JUPYTER_LAB

In [2]:
df = pd.read_csv('data/daily_confirmed.csv')
df.set_index(pd.to_datetime(df['日期']), inplace=True)

In [3]:
print('数据量:', df.shape[0])
print('数据时间:', df.index.min().date(), df.index.max().date())

数据量: 247
数据时间: 2020-01-20 2020-09-22


In [4]:
df.head(3)

日期   湖北  香港  广东  浙江  河南  湖南  安徽  上海  黑龙江  ...  海南  甘肃  吉林  \
日期                                                           ...               
2020-01-20  2020-1-20  270   0  14   0   0   0   0   1    0  ...   0   0   0   
2020-01-21  2020-1-21  375   0  23   5   1   1   0   9    0  ...   0   0   0   
2020-01-22  2020-1-22  444   1  32  27   5   9   4  16    1  ...   4   0   0   

            贵州  宁夏  澳门  青海  西藏  累计确诊  每日新增  
日期                                          
2020-01-20   0   0   0   0   0   290   290  
2020-01-21   0   0   0   0   0   435   145  
2020-01-22   1   1   1   0   0   588   153  

[3 rows x 37 columns]

In [5]:
def addDailyMap(df) -> Map:
    province = df.index.values[1:-2].tolist()
    values = df.values[1:-2].astype('int').tolist()
    date = df.values[0]
    m = (
        Map(
            init_opts=opts.InitOpts()
        )
        .add('累计确诊数量', [list(z) for z in zip(province, values)], 'china', is_map_symbol_show=False)
        .set_series_opts(label_opts=opts.LabelOpts(is_show=True))
        .set_global_opts(
            title_opts=opts.TitleOpts(title='中国各省新冠肺炎累计确诊数量', subtitle=date, pos_left='center'),
            legend_opts=opts.LegendOpts(is_show=False),
            visualmap_opts=opts.VisualMapOpts(
                is_piecewise=True,
                pieces=[
                    {"max": 100, "color": '#ffeead', 'label': '小于100人'},
                    {"min": 100, "max": 500, 'color': '#f29c2b', 'label': '100-500人'},
                    {"min": 500, "max": 1000, 'color': '#d9534f', 'label': '500-1000人'},
                    {"min": 1000, "max": 2000, "color":'#de4307', 'label': '1000-2000人'},
                    {"min": 2000, 'color': '#dd0a35', 'label': '2000人以上'}
                ]
            )
        )
    )
    return m

In [6]:
def getMapTimeline(df):
    t = (
        Timeline(init_opts=opts.InitOpts())
        .add_schema(play_interval=500)
    )
    for date in df.index:
        t.add(addDailyMap(df.loc[date]), date.date())
    return t

In [7]:
t = getMapTimeline(df)
t.load_javascript()

In [8]:
t.render_notebook()

# 通过交互分析可以发现：

## 现存确诊人数图

- 在1.20日左右，全国公布的疫情一开始出现在广东、湖北、北京上海等地，此时湖北的疫情确诊人数已经突破200；
- 此后，疫情从湖北开始向四周身份成扩散趋势，在1.26日湖北的确诊人数已经突破1000；除湖北外，浙江与广东确诊人数也到达三位数；国外在美国、澳大利亚、法国和泰国等东南亚国家也出现确诊病例；
- 在2.2日前后，湖北的确诊人数突破五位数，其他地区疫情人数继续增加；国外疫情也在欧洲、东南亚、美洲呈缓慢扩散趋势
- 在2月中旬，西藏成为国内首个清零的省份；国外继续缓慢增长；国内疫情迎来拐点，现存确诊人数趋于平缓、不再增加，并开始缓慢减少；现存确诊人数约为50000左右，其中大部分集中在湖北；
二月底三月初，国内确诊人数逐渐减少，国外此时开始大规模出现感染并扩散到多个国家；此时意大利、伊朗疫情较为严重；疫情开始扩散到非洲、南美洲；
三月中旬后，国内疫情已经基本得到控制，大多省份恢复到个位数或清零，绝大多数现存确诊病例集中在湖北；而世界上大部分国家都已出现确诊报告，许多国家突破五位数确诊；其中欧洲和伊朗、美国较为严重；
四月初，国内确诊人数继续减少，但有部分省份出现略微反扑；国外疫情几乎已经扩散到世界所有国家，其中美国确诊人数已经突破20万，是世界最严重的地区；
从四月中旬开始，由于外来输入原因，国内黑龙江及东北地区出现了一次比较严重的疫情反扑，确诊人数接近500，但在五月初逐步得到控制；
国外疫情在四五月份继续趋向严重，在5.8美国的确诊人数突破百万；但部分早期疫情严重的国家由于采取了有效的控制手段导致疫情缓解；

## 累计死亡人数

二月初，世界各国开始出现死亡病例；
国内的死亡病例数在二月中旬趋向平缓；
在三月中旬，世界各国死亡病例陆续出现或开始明显增多；
在五月份，报告的死亡数以美国、欧洲最为严重，许多国家死亡人数已经远远超过了中国；

## 死亡率：

死亡率也可以反应出疫情的控制程度，死亡率越低表明患者得到救治的概率越大；
在医疗资源充足的地区，死亡率可以降低到1%左右；医疗资源不足的地区，死亡率可以高达10%；
国内死亡率数据分析：
在一月下旬，中国的死亡率以黑龙江、湖北、湖南河南较为严重，但在一月底二月初除湖北外，其他省份呈下降趋势；
在国内疫情确诊人数峰值的二月中旬，国内平均死亡率为2.5，死亡率相对较高的是湖北、黑龙江、海南、台湾等地；
此后，国内湖北的死亡率继续升高，可能是由于医疗资源不足，无法给予患者有效救治，同时此前积累的确诊患者也陆续出现死亡；同样升高的有新疆、黑龙江；
三月中旬后，在国内疫情基本得到控制的情况下，全国平均死亡率在4%，湖北死亡率达到4.7左右；
在四月中旬补统计了一下之前因为新冠去世但未计入死亡率数据的死亡人数，最后湖北的死亡率为6.6，国内平均死亡率在5.5
国外死亡率数据分析：
从三月下旬开始，伴随着疫情的大规模扩散，各国疫情死亡率也逐步增高；
值得注意的是，许多国家的统计数据表明在其疫情刚开始出现的数日内死亡率是一个高峰，可能表明了在初始阶段未能对患者作出良好的检测和发现，只能从新冠重症患者处得到资料；
虽然非洲等某些不发达国家的疫情报告数据较少，但死亡率较高；可能表明了对于新冠的轻症患者，并没有良好的检测能力；
死亡率较高的国家显著集中在欧洲地区，表明了医疗资源的相对短缺；墨西哥的死亡率也较高；
总体来看：

中国在三月份就逐步控制住了疫情趋势，为世界抗疫事业做出了卓越的典范；
欧洲和美洲等发达国家疫情数据较为严重，可能是发达国家在世界范围内流动的人口较大，但更可能是发达国家能得到有效的检测并报告病例；

In [9]:
def addDailyBar(df) -> Bar:
    province = df.index[1:-2].values.tolist()
    values = df.values[1:-2].astype('int').tolist()
    data = [list(z) for z in zip(province, values)]
    data.sort(key=lambda x:x[1])
    
    bar = (
        Bar(
            init_opts=opts.InitOpts()
        )
        .add_xaxis([t[0] for t in data])
        .add_yaxis('累计确诊', [t[1] for t in data])
        .reversal_axis()
        .set_series_opts(label_opts=opts.LabelOpts(position='right'))
        .set_global_opts(
            title_opts=opts.TitleOpts(title='中国各省新冠肺炎累计确诊数量', subtitle=df.values[0], pos_left='35%'),
            legend_opts=opts.LegendOpts(pos_right='10%', pos_bottom='10%'),
            tooltip_opts=opts.TooltipOpts(trigger='axis')
        )
    )
    return bar

In [10]:
t = (
    Timeline(init_opts=opts.InitOpts(width='1100px', height='800px'))
    .add_schema(play_interval=500)
)
for date in df.index:
    bar = addDailyBar(df.loc[date])
    t.add(bar, date.date())
t.load_javascript()

In [11]:
t.render_notebook()

In [12]:
def aggByDate() -> Bar:
    barDf = df.loc[:, '每日新增']
    x_data = barDf.index.date.tolist()
    
    bar = (
        Bar()
        .add_xaxis(x_data)
        .add_yaxis(
            series_name='每日新增',
            y_axis=barDf.values.tolist()
        )
        .set_series_opts(label_opts=opts.LabelOpts(is_show=False))
#         .extend_axis(
#             yaxis=opts.AxisOpts(
#                 type_='value',
#                 name='新增数',
#                 min_=0,
#                 max_=16000,
#                 position='right',
#                 splitline_opts=opts.SplitLineOpts(
#                     is_show=True, linestyle_opts=opts.LineStyleOpts(opacity=1)
#                 ),
#             )
#         )
        .set_global_opts(
            title_opts=opts.TitleOpts('中国新冠肺炎累计确诊数量走势图', pos_left='35%'),
            tooltip_opts=opts.TooltipOpts(trigger='axis', axis_pointer_type='cross'),
            legend_opts=opts.LegendOpts(pos_right='10%', pos_bottom='15%')
        )
    )
    
    lineDf = df.loc[:, '累计确诊']
    line = (
        Line()
        .add_xaxis(x_data)
        .add_yaxis(
            series_name='累计确诊', 
            y_axis=lineDf.values.tolist(),
            label_opts=opts.LabelOpts(is_show=False)
        )
    )
    
    bar.overlap(line)
    
    return bar

In [13]:
bar = aggByDate()
bar.load_javascript()

In [14]:
bar.render_notebook()